In [1]:
%matplotlib inline
%load_ext autoreload
%autoreload 2
%config InlineBackend.figure_format = 'retina'

import numpy as np
from collections import defaultdict
import matplotlib.pyplot as plt
import seaborn as sns
from mle_toolbox import load_result_logs, visualize
from neuroevobench.metrics import plot_rliable

<frozen importlib._bootstrap>:228: RuntimeWarning: scipy._lib.messagestream.MessageStream size changed, may indicate binary incompatibility. Expected 56 from C header, got 64 from PyObject


envpool not installed, Atari problems will not work.
envpool not installed, Atari problems will not work.
You need to install brax for Brax tasks:
  pip install git+https://github.com/google/brax.git@main


### Helper to load and normalize results

In [2]:
result_dirs = [
               "../experiments/fmnist_classify/eval/",
               "../experiments/mnist_generate/eval/",
               "../experiments/ant/eval/",
               "../experiments/fetch/eval/",
               "../experiments/addition/eval/",
               "../experiments/smnist/eval/",
               "../experiments/asterix/eval/",
               "../experiments/breakout/eval/",
               "../experiments/cifar/eval/"
               ]

strategy_names = ['OpenES', 'PGPE', 'ARS', 'SNES', 'Sep_CMA_ES', 'LES',
                  'SimpleGA', 'SAMR_GA', 'GESMR_GA', 'LGA']
color_palette = sns.color_palette("colorblind", n_colors=len(strategy_names))

In [3]:
def load_and_normalize(log_path, normalize_by="OpenES"):
    meta_log, hyper_log = load_result_logs(log_path, aggregate_seeds=True)
    min_perf = hyper_log.test_eval_perf.min()
    max_perf = hyper_log.test_eval_perf.max()
    
    results_dict = {}
    for i, s in enumerate(hyper_log.strategy_name):
        results_dict[s] = hyper_log.test_eval_perf[i]

    for k, v in results_dict.items():
        results_dict[k] = (v - min_perf) / (max_perf - min_perf)
    
    norm_perf = float(results_dict[normalize_by])
    for k, v in results_dict.items():
        results_dict[k] = v / norm_perf

    return results_dict

    
all_dicts = []
for dir in result_dirs:
    d = load_and_normalize(dir, normalize_by="OpenES")
    all_dicts.append(d)

dd = defaultdict(list)

for d in all_dicts:
    for key, value in d.items():
        dd[key].append(value)

score_dict = dict(dd)

for k, v in score_dict.items():
    score_dict[k] = np.array(v).reshape(-1, 1)

del score_dict["OpenES"]

/Users/rob/anaconda3/envs/mle-toolbox/lib/python3.9/site-packages/numpy/lib/function_base.py:4650: UserWarning: Warning: 'partition' will ignore the 'mask' of the MaskedArray.
  arr.partition(
/Users/rob/anaconda3/envs/mle-toolbox/lib/python3.9/site-packages/numpy/lib/function_base.py:4488: RuntimeWarning: invalid value encountered in add
  lerp_interpolation = asanyarray(add(a, diff_b_a * t, out=out))


### Load Hyper & Meta-Log

In [4]:
plot_rliable(score_dict, "iqm", reps=100)

(<Figure size 3600x6000 with 1 Axes>,
 <Axes: title={'center': 'Interquartile Mean (IQM)'}, xlabel='OpenES Norm. Performance'>)

# Per Seed Results Loading

In [5]:
def score_normalization(scores, min_score, max_score):
  norm_score = (scores - min_score)/(max_score - min_score)
  return norm_score


def load_and_normalize(log_path):
    meta_log, hyper_log = load_result_logs(log_path, aggregate_seeds=True)
    seeds = hyper_log.seeds.iloc[0]
    openai_id = hyper_log[hyper_log.strategy_name == "OpenES"].run_id.iloc[0]
    min_perf = meta_log[openai_id].stats.test_eval_perf.mean[0]
    max_perf = meta_log[openai_id].stats.test_eval_perf.mean[-1]
    meta_log, hyper_log = load_result_logs(log_path, aggregate_seeds=False)

    results_dict = {}
    for i, s in enumerate(hyper_log.strategy_name):
        all_scores = []
        for sid in seeds:
          str_id = hyper_log[hyper_log.strategy_name == s].run_id.iloc[0]
          perf = meta_log[str_id]["seed_" + str(sid)].stats.test_eval_perf[-1]
          all_scores.append(perf)
        results_dict[s] = score_normalization(np.array(all_scores), min_perf, max_perf)

    return results_dict

In [6]:
load_and_normalize("../experiments/fmnist_classify/eval/")

{'OpenES': array([1.00034  , 1.0038697, 0.9994249, 1.0028237, 0.993542 ],
       dtype=float32),
 'PGPE': array([0.99746394, 0.9901431 , 0.99981695, 0.9944571 , 0.99458784],
       dtype=float32),
 'ARS': array([0.9735404 , 0.97785455, 0.9722332 , 0.96909565, 0.9756321 ],
       dtype=float32),
 'SNES': array([0.9868748 , 0.98582894, 0.9856982 , 0.97916174, 0.9839988 ],
       dtype=float32),
 'Sep_CMA_ES': array([0.97667795, 0.9740634 , 0.9744555 , 0.98033834, 0.96935713],
       dtype=float32),
 'LES': array([0.9518393, 0.9430806, 0.9498784, 0.9511857, 0.9458259],
       dtype=float32),
 'SimpleGA': array([0.75509197, 0.74319565, 0.6846289 , 0.70933676, 0.7409732 ],
       dtype=float32),
 'SAMR_GA': array([0.9400738, 0.939943 , 0.9421655, 0.937067 , 0.939943 ],
       dtype=float32),
 'GESMR_GA': array([0.9203337, 0.916281 , 0.9113134, 0.9170654, 0.8764087],
       dtype=float32),
 'LGA': array([0.82111025, 0.8162732 , 0.7933956 , 0.80895245, 0.8205872 ],
       dtype=float32)}

In [7]:
def load_norm_pipe(result_dirs):
    all_dicts = []
    for dir in result_dirs:
        d = load_and_normalize(dir)
        all_dicts.append(d)
    dd = defaultdict(list)

    for d in all_dicts:
        for key, value in d.items():
            dd[key].append(value)

    score_dict = dict(dd)

    for k, v in score_dict.items():
        score_dict[k] = np.stack(v)
    
    # Delete baseline OpenES
    del score_dict["OpenES"]

    # Rename keys with under score for nice labels
    score_dict['Sep-CMA-ES'] = score_dict['Sep_CMA_ES'] 
    score_dict['SAMR-GA'] = score_dict['SAMR_GA'] 
    score_dict['GESMR-GA'] = score_dict['GESMR_GA'] 
    del score_dict["Sep_CMA_ES"]
    del score_dict["SAMR_GA"]
    del score_dict["GESMR_GA"]
    return score_dict

In [8]:
score_dict = load_norm_pipe(result_dirs)
plot_rliable(score_dict, "iqm", reps=100)

(<Figure size 3600x6000 with 1 Axes>,
 <Axes: title={'center': 'Interquartile Mean (IQM)'}, xlabel='OpenES Norm. Performance'>)

# Aggregate results by Problem Classes

In [9]:
vision_dirs = [
               "../experiments/fmnist_classify/eval/",
               "../experiments/mnist_generate/eval/",
               "../experiments/cifar/eval/"
               ]

control_dirs = [
               "../experiments/ant/eval/",
               "../experiments/fetch/eval/",
               "../experiments/asterix/eval/",
               "../experiments/breakout/eval/",
               ]

sequence_dirs = [
               "../experiments/addition/eval/",
               "../experiments/smnist/eval/",
                ]

In [10]:
# Vision task results
score_dict = load_norm_pipe(vision_dirs)
plot_rliable(score_dict, "iqm", reps=100)

(<Figure size 3600x6000 with 1 Axes>,
 <Axes: title={'center': 'Interquartile Mean (IQM)'}, xlabel='OpenES Norm. Performance'>)

In [11]:
# Control task results
score_dict = load_norm_pipe(control_dirs)
plot_rliable(score_dict, "iqm", reps=100)

(<Figure size 3600x6000 with 1 Axes>,
 <Axes: title={'center': 'Interquartile Mean (IQM)'}, xlabel='OpenES Norm. Performance'>)

In [12]:
# Sequence task results
score_dict = load_norm_pipe(sequence_dirs)
plot_rliable(score_dict, "iqm", reps=100)

(<Figure size 3600x6000 with 1 Axes>,
 <Axes: title={'center': 'Interquartile Mean (IQM)'}, xlabel='OpenES Norm. Performance'>)

# Visualize Extra HPO-B & BBOB Results

In [24]:
# Redefine helpers with BayesianOpt supplementary results

def load_and_normalize(log_path):
    eo_path = os.path.join(log_path, "eval")
    meta_log, hyper_log = load_result_logs(eo_path, aggregate_seeds=True)
    seeds = hyper_log.seeds.iloc[0]
    openai_id = hyper_log[hyper_log.strategy_name == "OpenES"].run_id.iloc[0]
    min_perf = meta_log[openai_id].stats.test_eval_perf.mean[0]
    max_perf = meta_log[openai_id].stats.test_eval_perf.mean[-1]
    meta_log, hyper_log = load_result_logs(eo_path, aggregate_seeds=False)

    results_dict = {}
    for i, s in enumerate(hyper_log.strategy_name):
        all_scores = []
        for sid in seeds:
          str_id = hyper_log[hyper_log.strategy_name == s].run_id.iloc[0]
          perf = meta_log[str_id]["seed_" + str(sid)].stats.test_eval_perf[-1]
          all_scores.append(perf)
        results_dict[s] = score_normalization(np.array(all_scores), min_perf, max_perf)
    
    bo_path = os.path.join(log_path, "eval_bo")
    meta_log, hyper_log = load_result_logs(bo_path, aggregate_seeds=False)
    all_scores = []
    seeds = hyper_log.seeds.iloc[0]
    for sid in seeds:
        str_id = hyper_log[hyper_log.strategy_name == "BayesOptJAX"].run_id.iloc[0]
        perf = meta_log[str_id]["seed_" + str(sid)].stats.test_eval_perf[-1]
        all_scores.append(perf)
    results_dict["BayesOpt"] = score_normalization(np.array(all_scores), min_perf, max_perf)
    return results_dict

In [25]:
# Sequence task results
hpob_dir = ["../experiments/hpob/"]
score_dict = load_norm_pipe(hpob_dir)

for k in score_dict.keys():
    score_dict[k] = score_dict[k].reshape(-1, 1)

plot_rliable(score_dict, "iqm", reps=100)

/Users/rob/anaconda3/envs/mle-toolbox/lib/python3.9/site-packages/numpy/lib/function_base.py:4650: UserWarning: Warning: 'partition' will ignore the 'mask' of the MaskedArray.
  arr.partition(


[176588, 363028, 381632, 562958, 924197]


(<Figure size 3600x6000 with 1 Axes>,
 <Axes: title={'center': 'Interquartile Mean (IQM)'}, xlabel='OpenES Norm. Performance'>)

In [43]:
# Collect all BBOB results to normalize
fn_names = [
    "Sphere_mean",
    "EllipsoidalOriginal_mean",
    "RastriginOriginal_mean",
    "BuecheRastrigin_mean",
    "LinearSlope_mean",
    "AttractiveSector_mean",
    "StepEllipsoidal_mean",
    "RosenbrockOriginal_mean",
    "RosenbrockRotated_mean",
    "EllipsoidalRotated_mean",
    "Discus_mean",
    "BentCigar_mean",
    "SharpRidge_mean",
    "DifferentPowers_mean",
    "RastriginRotated_mean",
    "Weierstrass_mean",
    "SchaffersF7_mean",
    "SchaffersF7IllConditioned_mean",
    "GriewankRosenbrock_mean",
    "Schwefel_mean",
    "Lunacek_mean",
    "Gallagher101Me_mean",
    "Gallagher21Hi_mean",
]

In [41]:
hyper_log.strategy_name == s_name

0    False
Name: strategy_name, dtype: bool

In [46]:
strategy_names = ['OpenES', 'PGPE', 'ARS', 'SNES', 'Sep_CMA_ES', 'LES',
                  'SimpleGA', 'SAMR_GA', 'GESMR_GA']
results_dict = {k: [] for k in strategy_names}
results_dict["BayesOpt"] = []

for fn in fn_names:
    temp_results = []
    meta_log, hyper_log = load_result_logs(
    "../experiments/bbob/eval", aggregate_seeds=True)

    for s_name in strategy_names:
        run_id = hyper_log[hyper_log.strategy_name == s_name].run_id.values[0]
        temp_results.append(- meta_log[run_id].stats[fn].mean)
    
    meta_log, hyper_log = load_result_logs(
        "../experiments/bbob/eval_bo", aggregate_seeds=True)
    run_id = hyper_log[hyper_log.strategy_name == "BayesOptJAX"].run_id.values[0]
    temp_results.append(- meta_log[run_id].stats[fn].mean)
    
    v = np.array(temp_results)
    # Normalize into [0-1] range
    norm_results = (v - v.min()) / (v.max() - v.min())
    for i, s_name in enumerate(strategy_names):
        results_dict[s_name].append(norm_results[i])
    results_dict["BayesOpt"].append(norm_results[i + 1])

for s_name in strategy_names:
    results_dict[s_name] = np.array(results_dict[s_name]).reshape(-1, 1)
results_dict["BayesOpt"] = np.array(results_dict["BayesOpt"]).reshape(-1, 1)

results_dict['Sep-CMA-ES'] = results_dict['Sep_CMA_ES'] 
results_dict['SAMR-GA'] = results_dict['SAMR_GA'] 
results_dict['GESMR-GA'] = results_dict['GESMR_GA']
del results_dict["Sep_CMA_ES"]
del results_dict["SAMR_GA"]
del results_dict["GESMR_GA"]

In [47]:
plot_rliable(results_dict, "iqm", reps=100, xlabel="Normalized Score")

(<Figure size 3600x6000 with 1 Axes>,
 <Axes: title={'center': 'Interquartile Mean (IQM)'}, xlabel='Normalized Score'>)